# Modeling

Die eigentliche Modellierung nimmt im Analytics-Prozess oftmals weniger Zeit ein als zu Anfang angenommen. Dennoch ist es der zentrale Schritt und auch ein Fokusthema in diesem Kurs. Auf die operative Erstellung von Modellen wird daher in diesem Kapitel nicht eingangen. Eine Übersicht der verschiedenen Arten von Analytics-Modellen haben wir bereits in der Einführung gegeben. Betrachten wir hier einige Abwägungen, die bei der Modellauswahl zu treffen sind, und einige der typischen Fehler, die bei der Modellierung auftreten.

## Trade-Offs

Es gibt eine Vielzahl an verschiedenen Algorithmen um Modelle zu erzeugen. Beispielsweise bringt scikit-learn eine ganze Reihe von Algorithmen bereit und eine passende [Entscheidungshilfe](https://scikit-learn.org/stable/tutorial/machine_learning_map/index.html). Es stehen aber noch weitere Methoden zur Auswahl, z.B. [XGBoost](https://xgboost.ai) oder neuronale Netze mit [TensorFlow](http://tensorflow.org). Neben der Eignung für die zu lösende Analytics-Fragestellung und die vorhandenen Daten gibt es weitere Abwägungen, die getroffen werden müssen. Hier gilt es beispielsweise Trade-Offs zwischen der erzielbaren Genauigkeit und den folgenden Anforderungen einzugehen:
- Interpretierbarkeit: Komplexere Methoden können oft zu genaueren Ergebnissen führen jedoch leidet die Nachvollziehbarkeit warum bestimmte Ergebnisse erzielt werden. Die Nachvollziehbarkeit kann insbesondere wichtig sein für Compliance, Akzeptanz und Ethik.
- Ressourcen-Effizienz: Soll das Modell in embedded Geräten mit begrenzter Leistung und/oder Energiebudget (z.B. Smartphone) eingesetzt werden oder ist eine sehr große Menge an Vorhersagen zu machen oder eine sehr hohe Geschwindigkeit erforderlich, dann muss die verfügbare Rechenkapazität berücksichtigt werden. Beispielsweise muss ein Verkehrsassistent im Auto innerhalb von Sekundenbruchteilen ein Ergebnis liefern.
- Robustheit: Sehr genaue Modelle erkennen detaillierte Muster in den Trainingsdaten, die ggfs. nicht so gut auf neue bisher nicht gesehene Daten verallgemeinert werden können. Robustheit kann insbesondere wichtig sein, wenn ein Modell in unterschiedlichen Situationen eingesetzt werden soll (z.B. verschiedene Länder, bei sich änderndem Kundenverhalten, ...)

## Typische Fehler

### Overfitting und Underfitting

Beim Overfitting wird das Modell zu sehr an die Trainingsdaten angepasst wird. Dabei wird auch zufälliges Rauschen als Muster interpretiert oder nicht verallgemeinerbare Zusammenhänge gelernt. Beispielsweise werden Eigenschaften einer Produktnummer oder einem Kalenderdatum zugeschrieben - diese sind aber ggfs. eindeutig für ein einzelnes Ereignis und lassen sich somit nicht für weitere Vorhersagen nutzen. Modelle, die overfitted sind, liefern oft sehr gute Ergebnisse in der Evaluation auf bekannten Daten aber funktionieren sehr schlecht auf neuen Daten.

Häufige Ursache ist die eine fehlende Trennung der Trainings- und Test-Daten (siehe nächster Punkt). Das heisst die Modellgüte wird anhand der Daten bewertet, die auch schon ins Training eingeflossen sind. Dabei wird das Modell "belohnt", wenn es die Daten möglichst präzische "auswändig lernt".

Beim Underfitting hingegen wird die Varianz der Daten nicht ausreichend abgebildet. Hierzu kommt es insbesondere, wenn ein Modell gewählt wird, dass nicht zu den Daten passt, z.B.:
Zusammenhang, der erst ansteigt und dann abfällt (z.B. Beliebtheit von Urlaubszielen in Abhängigkeit der Entfernung zum Wohnort - zu nah ist langweilig, zu weit ist teuer/aufwändig) wird mit linearen Modell gelernt. Das lineare Modell bildet einfach eine Linie durch den Mittelwert (im Beispiel heißt das die Entfernung hat keinen Einfluss). 

### Falsche Trennung von Trainings- und Test-Daten

Die extremste Ausprägung ist, wenn überhaupt keine Trennung vorgenommen wurde. Letztendlich kann man hier nicht mehr von einer Vorhersage sprechen, wenn der Algorithmus, die vorherzusagenden Daten schon gesehen hat. Sämtliche Metriken, die zur Bewertung des Modells berechnet werden sind nutzlos.

Ein weiterer Fehler ist, wenn die Trennung nicht zufällig erfolgt ist, sondern zum Beispiel die ersten 70% der Daten für das Training und die restlichen 30% fürs Testen verwendet wurden. Jeder Datensatz, der nicht explizit in eine zufällige Reihenfolge gesetzt wurde, ist in irgendeiner Art sortiert. Eine Trennung nach Reihenfolge wird also die Vergleichbarkeit und Repräsentanz der Trainingsdaten mit den gesamten Daten untergraben. Beispielsweise kann eine Tabelle von Mitarbeitern sortiert sein nach:
- Reihenfolge des Hinzufügens. Dies entspricht wahrscheinlich der Reihenfolge des Betriebseintritts. In den Trainingsdaten befinden sich vor allem langgediente Mitarbeiter.
- Mitarbeiternummer - oftmals ebenso vergeben nach Einstiegsdatum
- Alter - in den Trainingsdaten befinden sich vor allem junge Mitarbeiter
- Name - ggfs. ist die Anfangsbuchstabenverteilung nicht gleich über verschiedene Generationen oder Nationalitäten
- Postleitzahl - Entfernung zum Arbeitsplatz kann hierdurch starkt beinflusst sein
- Weitere, z.B. Hierarchielevel, Abteilungsname, Gehalt, Kennzeichen des Firmenwagens, ...

Eine Ausnahme gilt für Zeitreihen. Hier wird meist eine Trennung an einer festen Datumsgrenze genommen. Alles was vor der Grenze liegt wird für das Training verwendet, alles danach für den Test. Dies hat zwei Gründe: es bildet die Vorhersagesituation ab, wo basierend auf vergangenen Daten die Zukunft vorhergesagt wird und Zwischenwerte sind oft leicht zu interpolieren aus den vorhergehenden und nachfolgenden Werten.

### Leakage des Zielwerts

Hier wird ein Feature verwendet, das zum Vorhersagezeitpunkt nicht bekannt ist und sehr stark mit dem Zielwert korreliert. Wenn wir z.B. Vorhersagen wollen, ob eine bestimmte Person von einer bestimmten Krankheit betroffen ist, dann könnte es ein Leakage, wenn wir ein Feature verwenden, das die Einnahme eines relevanten Medikaments beschreibt.

### Optimerung rein nach statistischen Güte-Maßen

Bei der Modellauswahl oder Feinjustierung werden häufig statistische Güte-Maße verwendet, z.B. die Präzision einer Klassifikation. Dies ist prinzipiell notwendig aber es sollte immer berücksichtigt werden:
- Die Güte-Maße bilden nicht den Erfolg des Modells in der Praxis ab
- Zu gute Werte in einem Güte-Maße führen häufig zu sehr schlechten Werten in anderen Maßen

Beispielsweise bei der Vorhersagen, ob ein Patient eine bestimmte Krankheit hat, kann
- Precision wichtig sein. Das heißt der Anteil der tatsächlichen Kranken an den als krank klassifizierten Patienten. Das ist wichtig, wenn die Nebenwirkungen oder Kosten einer Behandlich relativ hoch sind im Vergleich zur Auswirkung der Krank.
- Recall wichtig sein. Das heißt der Anteil der tatsächlich Kranken, die vom Modell erkannt wurden. Das ist wichtig, wenn die Auswirkungen der Krankheit, die Nebenwirkungen/Kosten einer Behandlung weit übersteigen.

Diese beiden Güte-Maße stehen im Widerspruch. Beispielsweise kann der Recall auf 100% gesetzt werden indem man einfach alle Patienten als krank klassifiziert. Darunter leidet die Precision, da nun viele falsch Positive erzeugt werden, d.h. viele nicht-kranke, die als krank eingeordnet werden.

### Interpretation von Modellergebnissen als präzise Vorhersagen

Modelle können meist keine präzisen Vorhersagen machen. Das Modell lernt Muster aus der Vergangenheit und wählt dann die passendensten Muster zu den gegebenen Informationen aus. Das Ergebnis unterliegt immer einen gewissen Wahrscheinlichkeitsverteilung. Jedoch werden Ergebnisse häufig als präzise Vorhersagen präsentiert oder interpretiert. Betrachten wir beispielsweise ein Modell zur Prognose von Abverkaufsmengen. Ein Ergebnis des Modells könnte sein: an vergangenen Samstagen mit ähnlichen Eigenschaften (Werte der Features) wurden in 50% der Fälle 20 Packungen Toilettenpapier oder weniger verkauft und in 90% der Fälle 30 Packungen oder weniger. Oftmals wird ein solches Ergebnis reduziert auf: am Samstag werden 20 Packungen verkauft (oder auch: 30 Packungen).

### Interpretation von Korrelation als Kausalität

Modell erkennen Muster im Sinne von: wenn A zutrifft, dann trifft mit einer hohen Wahrscheinlichkeit auch B zu. Der Mensch neigt dazu dies als Kausalität zu interpretieren: wegen A passiert B. Dies lässt sich aber im Allgemeinen nicht aus den Daten auslesen. Für Vorhersagen ist es auch nicht wichtig: es reicht über die Korrelation und den Wert von A Bescheid zu wissen. Gefährlich wird es, wenn nun A beeinflusst (verstärkt oder abgeschwächt) wird, um B zu beeinflussen. Die Korrelation kann aber auch auf einer gemeinsamen Ursache beruhen oder auch auf Zufallen. Die Webseite https://tylervigen.com listet viele solcher Korrelationen auf, wo man keinesfalls auf Kausalität schliessen sollte, z.B. der beinahe perfekte Zusammenhang der Scheidungsrate und dem Pro-Kopf-Verbrauch von Margarine im US-Bundesstaat Maine.

### Selection Bias ignorieren

Die Daten, die für ein Moell verwendet werden sind nur eine unvollständige Abbildung der Realität. So lange die Daten die gleichen Charakteristiken wie die Realität haben, ist das kein Problem. Durch die Art der Datenerhebung kann es aber zu systematischen Unterschieden zwischen Daten und Realität kommen, z.B.:
- Online-Reviews von Artikeln werden häufig von besonders zufriedenen oder unzufriedenen Kunden erstellt.
- Bei der Auswahl von Testgruppen (z.B. Mitarbeiter, Regionen, Abteilungen) werden häufig welche mit besonders guter Leistung oder mit besonders hohen Engagement oder mit niedriger Auslastung oder in Nähe des Hauptquartiers ausgewählt.

### Datenauswahl

Daten, die die Realität gut abbilden, können sehr umfangreich sein. Eine Einschränkung der benutzten Daten kann sinnvoll sein. Dabei sollte auf den Erhalt der Repräsentanz Wert gelegt werden. Um Trends in der gesundheitlichen Entwicklung der Kunden einer Krankenkasse zu finden könnte man die Daten einschränken:
- Alle Gesundheitsdaten über 1 Jahr für alle Patienten
- Nur Arzneimittel über 10 Jahre für alle Patienten
- Alle Gesundheitsdaten über 10 Jahre für ein Zehntel der Patienten
Am sinnvollsten erscheint der letzte Ansatz - jedoch nur wenn das Zehntel repräsentativ gewählt wird.

### Verschlechterung des Modells über die Zeit

Vorhersagemodelle lernen Muster in historischen Daten und wenden diese auf die Zukunft an unter der Annahme, dass die Zukunft sich gleich verhält wie die Vergangenheit. Dabei muss immer darauf geachtet werden, dass diese Annahme weiter besteht. Beispielsweise kann sich das Kundenverhalten ändern in Bezug auf Kaufentscheidungen, wenn der Wohlstand im Land sich ändert. Das Feature Qualität gewinnt eine größere Bedeutung als der Preis.

### Hinarbeiten auf vorher festgelegtes Ergebnis

Oftmals bestehen zu einer Fragestellung schon Meinungen basierend auf dem Erfahrungswissen von Mitarbeitern. Diese gilt es mit Daten zu hinterfragen und entweder zu bestätigen oder zu widerlegen. Es besteht aber immer die Gefahr, dass die Daten und die Analysen so lange hingedreht werden bis die vorgefertigen Meinungen von hochrangingen Führungskräften bestätigt werden. Beispielsweise könnte bei einer Kundensegmentierung so lange an den Features, deren Skalierung und Gewichtung optimiert werden bis genau die 5 Kundensegmente rauskommen, die der bisherigen Marketing-Strategie entsprechen